In [1]:
import tensorflow as tf
from tensorflow import keras
import numpy as np
import matplotlib.pyplot as plt
from keras.preprocessing import image
from PIL import Image
import cv2
import warnings
from keras.preprocessing.image import ImageDataGenerator  
warnings.filterwarnings('ignore')
import plotly.graph_objects as go
import plotly.subplots as sp

/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
train_data='/kaggle/input/arabic-letters-classification/Final_Arabic_Alpha_dataset/Final_Arabic_Alpha_dataset/train'
test_data='/kaggle/input/arabic-letters-classification/Final_Arabic_Alpha_dataset/Final_Arabic_Alpha_dataset/test'

In [3]:
g_width, img_height, img_width = 128, 128, 128  # Corrected variable names

batch_size = 32

train_datagen = ImageDataGenerator(
  rescale=1./255,
  shear_range=0.2,
  zoom_range=0.2,
  horizontal_flip=True,
  rotation_range=30,  # Add rotation for more diversity
  width_shift_range=0.2,
  height_shift_range=0.2,
  validation_split=0.2
)


train_generator = train_datagen.flow_from_directory(
    train_data,
    target_size=(img_height, img_width),  # Corrected target_size
    class_mode='categorical',
    shuffle=False
)

labels_dict = {class_name: label for label, class_name in train_generator.class_indices.items()}
print(labels_dict)


Found 42559 images belonging to 65 classes.
{0: '0', 1: '1', 2: '10', 3: '11', 4: '12', 5: '13', 6: '14', 7: '15', 8: '16', 9: '17', 10: '18', 11: '19', 12: '2', 13: '20', 14: '21', 15: '22', 16: '23', 17: '24', 18: '25', 19: '26', 20: '27', 21: '28', 22: '29', 23: '3', 24: '30', 25: '31', 26: '32', 27: '33', 28: '34', 29: '35', 30: '36', 31: '37', 32: '38', 33: '39', 34: '4', 35: '40', 36: '41', 37: '42', 38: '43', 39: '44', 40: '45', 41: '46', 42: '47', 43: '48', 44: '49', 45: '5', 46: '50', 47: '51', 48: '52', 49: '53', 50: '54', 51: '55', 52: '56', 53: '57', 54: '58', 55: '59', 56: '6', 57: '60', 58: '61', 59: '62', 60: '63', 61: '64', 62: '7', 63: '8', 64: '9'}


In [4]:
num_images = 10
num_images_per_row = 5
num_rows = int(np.ceil(num_images / num_images_per_row))
fig_images = sp.make_subplots(rows=num_rows, cols=num_images_per_row, subplot_titles=[f'Image {i+1}' for i in range(num_images)])

for i in range(num_images):
    row_position = i // num_images_per_row + 1
    col_position = i % num_images_per_row + 1

    gray_image = np.dot(train_generator[i][0][0], [0.2989, 0.5870, 0.1140])

    downsampled_image = gray_image[::-1, ::-1]

    fig_images.add_trace(
        go.Heatmap(z=downsampled_image.T, colorscale='inferno', opacity=1, colorbar=dict(showticklabels=False)),
        row=row_position,
        col=col_position
    )

fig_images.update_layout(
    title='Randomly Selected Images',
    font=dict(color='white'),
    paper_bgcolor='black',
    plot_bgcolor='black',
    showlegend=False,
    width=1200,
    height=300 * num_rows
)

fig_images.show()

In [5]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, BatchNormalization, Flatten, Dense, Dropout

model = Sequential()


In [6]:

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, BatchNormalization, Flatten, Dense, Dropout

model = Sequential()

model.add(Conv2D(64, (3, 3), padding="same", activation="relu", input_shape=(128, 128, 3)))
model.add(BatchNormalization())
model.add(Conv2D(64, (3, 3), activation="elu"))
model.add(BatchNormalization())
model.add(MaxPooling2D((2, 2)))

model.add(Conv2D(128, (3, 3), padding="same", activation="relu"))
model.add(BatchNormalization())
model.add(Conv2D(128, (3, 3), activation="tanh"))
model.add(BatchNormalization())
model.add(MaxPooling2D((2, 2)))

model.add(Conv2D(256, (3, 3), padding="same", activation="relu"))
model.add(BatchNormalization())
model.add(Conv2D(256, (3, 3), activation="sigmoid"))
model.add(BatchNormalization())
model.add(MaxPooling2D((2, 2)))

model.add(Flatten())

model.add(Dense(512, activation="relu"))
model.add(Dropout(0.5))
model.add(BatchNormalization())

model.add(Dense(len(train_generator.class_indices), activation="softmax"))

# Compile the model
model.compile(
 optimizer=tf.keras.optimizers.Adam(),
 loss='categorical_crossentropy',
 metrics=['accuracy']
)

# Build the model with a sample batch
sample_batch = next(train_generator)
model.build(input_shape=sample_batch[0].shape)


model.summary()


Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 128, 128, 64)      1792      
                                                                 
 batch_normalization (Batch  (None, 128, 128, 64)      256       
 Normalization)                                                  
                                                                 
 conv2d_1 (Conv2D)           (None, 126, 126, 64)      36928     
                                                                 
 batch_normalization_1 (Bat  (None, 126, 126, 64)      256       
 chNormalization)                                                
                                                                 
 max_pooling2d (MaxPooling2  (None, 63, 63, 64)        0         
 D)                                                              
                                                      

In [7]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, BatchNormalization, Flatten, Dense, Dropout
import tensorflow as tf

model = Sequential()

# Convolutional Blocks
for filters in [64, 128, 256]:
    model.add(Conv2D(filters, (3, 3), padding="same", activation="relu"))
    model.add(BatchNormalization())
    model.add(Conv2D(filters, (3, 3), padding="same", activation="relu"))
    model.add(BatchNormalization())
    model.add(MaxPooling2D((2, 2)))

# Example of adding more convolutional layers
for filters in [512, 512, 512]:
    model.add(Conv2D(filters, (3, 3), padding="same", activation="relu"))
    model.add(BatchNormalization())
    model.add(Conv2D(filters, (3, 3), padding="same", activation="relu"))
    model.add(BatchNormalization())
    model.add(MaxPooling2D((2, 2)))

# Fully Connected Layers
model.add(Flatten())
model.add(Dense(512, activation="relu"))
model.add(Dropout(0.5))
model.add(BatchNormalization())

# Output Layer
model.add(Dense(len(train_generator.class_indices), activation="softmax"))

# Compile the model
model.compile(
 optimizer=tf.keras.optimizers.Adam(),
 loss='categorical_crossentropy',
 metrics=['accuracy']
)

# Build the model with a sample batch
sample_batch = next(train_generator)
model.build(input_shape=sample_batch[0].shape)

# Build the model with a sample batch
sample_batch = next(train_generator)
model.build(input_shape=sample_batch[0].shape)

# Display the summary of the model
model.summary()


Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_6 (Conv2D)           (32, 128, 128, 64)        1792      
                                                                 
 batch_normalization_7 (Bat  (32, 128, 128, 64)        256       
 chNormalization)                                                
                                                                 
 conv2d_7 (Conv2D)           (32, 128, 128, 64)        36928     
                                                                 
 batch_normalization_8 (Bat  (32, 128, 128, 64)        256       
 chNormalization)                                                
                                                                 
 max_pooling2d_3 (MaxPoolin  (32, 64, 64, 64)          0         
 g2D)                                                            
                                                      

In [8]:
## from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.callbacks import EarlyStopping, LearningRateScheduler
import plotly.graph_objects as go

# Assuming img_width, img_height, batch_size, and train_data_dir are defined earlier

train_datagen = ImageDataGenerator(
  rescale=1./255,
  shear_range=0.2,
  zoom_range=0.2,
  horizontal_flip=True,
  rotation_range=30,  # Add rotation for more diversity
  width_shift_range=0.2,
  height_shift_range=0.2,
  validation_split=0.2
)


# Training generator
train_generator = train_datagen.flow_from_directory(
    train_data,
    target_size=(img_width, img_height),
    batch_size=batch_size,
    class_mode='categorical',
    shuffle=True,
    subset='training'  # Shuffle training data
)

# Validation generator
validation_generator = train_datagen.flow_from_directory(
    train_data,
    target_size=(img_width, img_height),
    batch_size=batch_size,
    class_mode='categorical',
    shuffle=True,  # Shuffle validation data
    subset='validation'
)

steps_per_epoch = train_generator.samples // batch_size

# early_stopping = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)

# Learning rate schedule
def lr_schedule(epoch):
    if epoch < 5:
        lr = 0.001
    elif epoch < 10:
        lr = 0.0005
    else:
        lr = 0.0001
    print(f'Learning Rate for epoch {epoch + 1}: {lr}')
    return lr

lr_scheduler = LearningRateScheduler(lr_schedule)
early_stopping = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)


history = model.fit(
    train_generator,
    epochs=20,  # Adjust the total number of epochs based on your needs
    steps_per_epoch=steps_per_epoch,
    validation_data=validation_generator,
    callbacks=[early_stopping, lr_scheduler],
    verbose=1,
    workers=4
)

evaluation = model.evaluate(train_generator, verbose=1)
print(f"Train Accuracy: {evaluation[1] * 100:.2f}%")

final_val_accuracy = history.history['val_accuracy'][-1]
print(f"Final Validation Accuracy: {final_val_accuracy}")

# Save the trained model
model.save('your_model.h5')


Found 34064 images belonging to 65 classes.
Found 8495 images belonging to 65 classes.
Learning Rate for epoch 1: 0.001
Epoch 1/20
1064/1064 [==============================] - 204s 176ms/step - loss: 3.5483 - accuracy: 0.1162 - val_loss: 26.8122 - val_accuracy: 0.0207 - lr: 0.0010
Learning Rate for epoch 2: 0.001
Epoch 2/20
1064/1064 [==============================] - 169s 158ms/step - loss: 2.2038 - accuracy: 0.3612 - val_loss: 2.6674 - val_accuracy: 0.3039 - lr: 0.0010
Learning Rate for epoch 3: 0.001
Epoch 3/20
1064/1064 [==============================] - 169s 159ms/step - loss: 1.7123 - accuracy: 0.4953 - val_loss: 3.7322 - val_accuracy: 0.1614 - lr: 0.0010
Learning Rate for epoch 4: 0.001
Epoch 4/20
1064/1064 [==============================] - 169s 158ms/step - loss: 1.4285 - accuracy: 0.5765 - val_loss: 2.9969 - val_accuracy: 0.3194 - lr: 0.0010
Learning Rate for epoch 5: 0.001
Epoch 5/20
1064/1064 [==============================] - 168s 158ms/step - loss: 1.2373 - accuracy: 0.63

In [9]:


fig = go.Figure()

fig.add_trace(go.Scatter(y=history.history['accuracy'], mode='lines', name='Training Accuracy'))
fig.add_trace(go.Scatter(y=history.history['loss'], mode='lines', name='Training Loss'))
fig.add_trace(go.Scatter(y=history.history['val_accuracy'], mode='lines', name='Validation Accuracy'))
fig.add_trace(go.Scatter(y=history.history['val_loss'], mode='lines', name='Validation Loss'))

fig.update_layout(title='Training History', xaxis_title='Epoch', template='plotly_dark')
fig.show()


In [10]:
import plotly.graph_objects as go

model_summary = []
model.summary(print_fn=lambda x: model_summary.append(x))

# Create a table trace
table_trace = go.Table(
    header=dict(values=['Layer (type)', 'output Shape', 'Param #'],
                fill_color='rgb(55, 55, 55)',
                font=dict(color='white')),
    cells=dict(values=[model_summary[1:], model_summary[2:11], model_summary[3:]],
               fill_color='rgb(35, 35, 35)',
               font=dict(color='white'))
)

# Create layout
layout = go.Layout(
    title='Model Summary',
    width=800,
    height=400,
    font=dict(color='white'),
    paper_bgcolor='rgb(0, 0, 0)',
    plot_bgcolor='rgb(0, 0, 0)'
)

# Create figure with the table trace
fig = go.Figure(data=table_trace, layout=layout)

# Show the figure
fig.show()


In [11]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=history.epoch,
                         y=history.history['accuracy'],
                         name='Accuracy'))
fig.add_trace(go.Scatter(x=history.epoch,
                         y=history.history['val_accuracy'],
                         name='Validation Accuracy'))
fig.update_layout(title='Training and Validation Accuracy',
                  xaxis_title='Epoch',
                  yaxis_title='Accuracy',
                  legend=dict(x=0.7, y=0.9),
                  width=800,
                  height=600,
                  plot_bgcolor='rgb(17, 17, 17)',
                  paper_bgcolor='rgb(17, 17, 17)',
                  font=dict(color='white'))
fig.show()


In [12]:
test_images = tf.keras.utils.image_dataset_from_directory(
        test_data,
        labels=None,
        label_mode="categorical",
        color_mode='grayscale',
        shuffle=False,
        image_size=(128, 128),
        batch_size=batch_size)


Found 10640 files belonging to 1 classes.


In [13]:
for images in test_images:
    print(images.shape)
    break

(32, 128, 128, 1)


In [14]:
import os
import numpy as np
from tensorflow.keras.preprocessing import image
from tensorflow.keras.models import load_model

# Load the trained model
# model = load_model('/kaggle/working/your_model.h5')  # Change the filename if necessary

# Define the path to the test data
test_data_path = '/kaggle/input/arabic-letters-classification/Final_Arabic_Alpha_dataset/Final_Arabic_Alpha_dataset/test'

# Get the list of images in the test data directory
test_images = os.listdir(test_data_path)

# Preprocess and make predictions for each test image
predictions = []

for img_name in test_images:
    img_path = os.path.join(test_data_path, img_name)
    
    # Load and preprocess the image
    img = image.load_img(img_path, target_size=(img_height, img_width))
    img_array = image.img_to_array(img)
    img_array = np.expand_dims(img_array, axis=0)
    img_array /= 255.0  # Rescale to [0, 1]

    # Make predictions
    prediction = model.predict(img_array)
    predicted_class = np.argmax(prediction)

    # Add the predicted class to the list
    predictions.append((img_name, predicted_class))

# Display the predictions
for img_name, predicted_class in predictions:
    print(f"Image: {img_name}, Predicted Class: {predicted_class}, Predicted Label: {labels_dict[predicted_class]}")


1/1 [==============================] - 0s 21ms/step
Image: 9273.png, Predicted Class: 6, Predicted Label: 14
Image: 9292.png, Predicted Class: 42, Predicted Label: 47
Image: 4353.png, Predicted Class: 26, Predicted Label: 32
Image: 7968.png, Predicted Class: 48, Predicted Label: 52
Image: 6490.png, Predicted Class: 39, Predicted Label: 44
Image: 5511.png, Predicted Class: 33, Predicted Label: 39
Image: 6262.png, Predicted Class: 38, Predicted Label: 43
Image: 2664.png, Predicted Class: 15, Predicted Label: 22
Image: 8419.png, Predicted Class: 51, Predicted Label: 55
Image: 9703.png, Predicted Class: 59, Predicted Label: 62
Image: 2539.png, Predicted Class: 14, Predicted Label: 21
Image: 9110.png, Predicted Class: 55, Predicted Label: 59
Image: 5703.png, Predicted Class: 34, Predicted Label: 4
Image: 1231.png, Predicted Class: 6, Predicted Label: 14
Image: 1017.png, Predicted Class: 5, Predicted Label: 13
Image: 4803.png, Predicted Class: 29, Predicted Label: 35
Image: 7197.png, Predict

In [15]:
img_list = os.listdir('/kaggle/input/arabic-letters-classification/Final_Arabic_Alpha_dataset/Final_Arabic_Alpha_dataset')


In [16]:
labels_list = sorted(os.listdir('/kaggle/input/arabic-letters-classification/Final_Arabic_Alpha_dataset/Final_Arabic_Alpha_dataset/train'))
print(labels_list)

['0', '1', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '2', '20', '21', '22', '23', '24', '25', '26', '27', '28', '29', '3', '30', '31', '32', '33', '34', '35', '36', '37', '38', '39', '4', '40', '41', '42', '43', '44', '45', '46', '47', '48', '49', '5', '50', '51', '52', '53', '54', '55', '56', '57', '58', '59', '6', '60', '61', '62', '63', '64', '7', '8', '9']
